In [1]:
from BinanceHttpClient import BinanceHttp, contractType, Interval, OrderSide, OrderType
import pandas as pd
import numpy as np
from datetime import datetime
import time
import traceback

In [2]:
def tsConverter(Year, Month, Day, Hour, Min, Second):
    ts= datetime(Year, Month, Day, Hour, Min, Second).timestamp()
    return int(ts)

In [3]:
start_time = tsConverter(2022, 7, 20, 1, 0, 0) * 1000
end_time = tsConverter(2022, 10, 20, 1, 3, 0) * 1000

In [4]:
print(start_time)
print(end_time)

1658250000000
1666198980000


In [25]:
httpClient = BinanceHttp(marketType = 'USDTFutures')
exchangeInfo = httpClient.get_exchange_info()
# symbol = [i['symbol'] for i in exchangeInfo['symbols'] if i['status'] != 'SETTLING' and i['symbol'] not in ['BTCUSDT_221230', 'ETHUSDT_221230']]
# print(symbol)
print(exchangeInfo)

{'timezone': 'UTC', 'serverTime': 1666332044974, 'futuresType': 'U_MARGINED', 'rateLimits': [{'rateLimitType': 'REQUEST_WEIGHT', 'interval': 'MINUTE', 'intervalNum': 1, 'limit': 2400}, {'rateLimitType': 'ORDERS', 'interval': 'MINUTE', 'intervalNum': 1, 'limit': 1200}, {'rateLimitType': 'ORDERS', 'interval': 'SECOND', 'intervalNum': 10, 'limit': 300}], 'exchangeFilters': [], 'assets': [{'asset': 'USDT', 'marginAvailable': True, 'autoAssetExchange': '-10000'}, {'asset': 'BTC', 'marginAvailable': True, 'autoAssetExchange': '-0.00100000'}, {'asset': 'BNB', 'marginAvailable': True, 'autoAssetExchange': '-10'}, {'asset': 'ETH', 'marginAvailable': True, 'autoAssetExchange': '-5'}, {'asset': 'XRP', 'marginAvailable': True, 'autoAssetExchange': '0'}, {'asset': 'ADA', 'marginAvailable': True, 'autoAssetExchange': '0'}, {'asset': 'DOT', 'marginAvailable': True, 'autoAssetExchange': '0'}, {'asset': 'SOL', 'marginAvailable': True, 'autoAssetExchange': '0'}, {'asset': 'BUSD', 'marginAvailable': True

In [11]:
historyFundRate = httpClient.get_historyFundRate(symbol = 'APTUSDT', start_time = 1658250000000, end_time = 1666198980000)

In [12]:
historyFundRate

[{'symbol': 'APTUSDT',
  'fundingTime': 1666108800000,
  'fundingRate': '0.00010000'},
 {'symbol': 'APTUSDT',
  'fundingTime': 1666137600007,
  'fundingRate': '0.00010000'},
 {'symbol': 'APTUSDT',
  'fundingTime': 1666166400022,
  'fundingRate': '-0.00750000'},
 {'symbol': 'APTUSDT',
  'fundingTime': 1666195200016,
  'fundingRate': '-0.00200030'}]

In [ ]:
maxRate = {}
for i in symbol:
    time.sleep(3)
    historyFundRate = httpClient.get_historyFundRate(symbol = i, start_time = 1658250000000, end_time = 1666198980000)
    maxRate[i]=max([abs(float(i['fundingRate'])*100) for i in historyFundRate ])
    
extractSymbol = [k for k, v in maxRate.items() if v > 1]
len(extractSymbol)

In [32]:
len(symbol)

188

In [39]:
httpClient = BinanceHttp(marketType = 'USDTFutures')
exchangeInfo = httpClient.get_exchange_info()
symbol = [i['symbol'] for i in exchangeInfo['symbols'] if i['status'] != 'SETTLING' and i['symbol'] not in ['BTCUSDT_221230', 'ETHUSDT_221230']]

# realTimeFundRate = httpClient.get_realTimeFundRate(symbol = "BTCUSDT")
columns = {'date': 0, 'open': 1, 'high': 2, 'low': 3, 'close': 4, 'volume': 5, "ts": 6}
final_dict = {}
testSymbol = ["BTCUSDT"]
threshold = 1/1000

for i in symbol[0:188]:
    time.sleep(1)
    historyFundRate = httpClient.get_historyFundRate(symbol = i, start_time = 1658250000000, end_time = 1666198980000)
    extractThreshold = [i for i in historyFundRate if abs(float(i['fundingRate'])) > threshold]
    print(i, ':', len(extractThreshold))
    if len(extractThreshold):
        fundRateDf = pd.DataFrame()
        fundRateDf[i] = [i['fundingRate'] for i in extractThreshold ]
        fundRateDf['ts'] = [int(i['fundingTime']/1000) for i in extractThreshold]
        kline_aggregator = []
        for j in fundRateDf['ts']:
            time.sleep(1)
            kline_start_time = j * 1000
            kline_end_time = (j + 900)*1000
            klineResp = httpClient.get_kline(symbol = i, interval=Interval.MINUTE_5, start_time = kline_start_time, end_time= kline_end_time, limit=1440)
            kline_aggregator+=klineResp
        klines = [[datetime.fromtimestamp(int(kline[0]/1000)).strftime('%Y-%m-%d, %H:%M:%S'),kline[1],kline[2],kline[3],kline[4],kline[5], int(kline[0]/1000)] for kline in kline_aggregator]     
        klineDf = pd.DataFrame(klines, columns = columns)
        mergeDf = pd.merge(klineDf, fundRateDf, how = 'left', on = 'ts')
        final_dict[i] = mergeDf
    else:
        continue

BTCUSDT : 0
ETHUSDT : 5
BCHUSDT : 0
XRPUSDT : 0
EOSUSDT : 0
LTCUSDT : 0
TRXUSDT : 0
ETCUSDT : 10
LINKUSDT : 0
XLMUSDT : 0
ADAUSDT : 0
XMRUSDT : 5
DASHUSDT : 0
ZECUSDT : 0
XTZUSDT : 0
BNBUSDT : 0
ATOMUSDT : 0
ONTUSDT : 1
IOTAUSDT : 1
BATUSDT : 0
VETUSDT : 0
NEOUSDT : 0
QTUMUSDT : 0
IOSTUSDT : 3
THETAUSDT : 0
ALGOUSDT : 0
ZILUSDT : 0
KNCUSDT : 11
ZRXUSDT : 1
COMPUSDT : 1
OMGUSDT : 0
DOGEUSDT : 0
SXPUSDT : 1
KAVAUSDT : 2
BANDUSDT : 1
RLCUSDT : 27
WAVESUSDT : 12
MKRUSDT : 1
SNXUSDT : 4
DOTUSDT : 0
DEFIUSDT : 2
YFIUSDT : 0
BALUSDT : 5
CRVUSDT : 0
TRBUSDT : 25
RUNEUSDT : 0
SUSHIUSDT : 0
SRMUSDT : 2
EGLDUSDT : 0
SOLUSDT : 0
ICXUSDT : 2
STORJUSDT : 1
BLZUSDT : 3
UNIUSDT : 0
AVAXUSDT : 0
FTMUSDT : 0
HNTUSDT : 19
ENJUSDT : 0
FLMUSDT : 10
TOMOUSDT : 1
RENUSDT : 0
KSMUSDT : 0
NEARUSDT : 0
AAVEUSDT : 0
FILUSDT : 0
RSRUSDT : 25
LRCUSDT : 0
MATICUSDT : 0
OCEANUSDT : 10
CVCUSDT : 2
BELUSDT : 7
CTKUSDT : 8
AXSUSDT : 8
ALPHAUSDT : 1
ZENUSDT : 0
SKLUSDT : 0
GRTUSDT : 0
1INCHUSDT : 1
BTCBUSD : 0
CHZUSDT :

In [68]:
finalDict

{'APTUSDT': []}

In [89]:
finalDict = {}
for i in final_dict.keys():
    tmpDict = final_dict[i]
    tmpDict[i] = tmpDict[i].replace(np.nan, 99)
    rate = 0
    closeList = []
    resultList=[]
    for index, row in tmpDict.iterrows():
        if len(closeList) == 3:
            resultList.append([rate, base, closeList])  
            rate = 0
            closeList = []
        if row[i] != 99:
            rate = float(row[i])
            base = float(row['high']) if float(row[i]) < 0 else float(row['low']) 
        else:
            closeList.append(float(row['close']))
    resultList.append([rate, base, closeList])  
    finalDict[i] = resultList

In [88]:
final_dict['ETHUSDT']

date     open     high      low    close      volume  \
0   2022-09-14, 08:00:00  1571.91  1572.36  1563.00  1565.15   50625.002   
1   2022-09-14, 08:05:00  1565.16  1573.00  1561.46  1572.81   37846.844   
2   2022-09-14, 08:10:00  1572.82  1576.39  1571.48  1575.01   24040.759   
3   2022-09-14, 08:15:00  1575.01  1575.27  1555.33  1557.47   53791.632   
4   2022-09-14, 16:00:00  1610.06  1610.15  1598.32  1599.30   50658.212   
5   2022-09-14, 16:05:00  1599.29  1603.00  1596.27  1602.37   33788.592   
6   2022-09-14, 16:10:00  1602.37  1604.28  1584.06  1588.54   67066.127   
7   2022-09-14, 16:15:00  1588.55  1593.66  1587.64  1589.81   36623.429   
8   2022-09-15, 00:00:00  1592.80  1596.76  1589.00  1592.17   46182.451   
9   2022-09-15, 00:05:00  1592.17  1593.26  1586.00  1589.31   37256.358   
10  2022-09-15, 00:10:00  1589.31  1590.49  1586.56  1588.76   14952.644   
11  2022-09-15, 00:15:00  1588.76  1590.57  1582.30  1585.45   31183.884   
12  2022-09-15, 08:00:00  1635.40  1639.03  1623.76  1629.70  112324.548   
13  2022-09-15, 08:05:00  1629.70  1635.48  1626.00  1633.60   36524.764   
14  2022-09-15, 08:10:00  1633.60  1636.00  1631.90  1634.25   17605.478   
15  2022-09-15, 08:15:00  1634.25  1640.31  1627.24  1636.90   49741.430   
16  2022-09-15, 16:00:00  1641.00  1641.00  1622.61  1628.37  145958.326   
17  2022-09-15, 16:05:00  1628.36  1632.55  1617.08  1621.25   77814.771   
18  2022-09-15, 16:10:00  1621.25  1626.00  1620.67  1623.85   34753.546   
19  2022-09-15, 16:15:00  1623.86  1625.66  1618.04  1618.30   33648.824   

            ts      ETHUSDT  
0   1663113600  -0.00111142  
1   1663113900           99  
2   1663114200           99  
3   1663114500           99  
4   1663142400  -0.00182506  
5   1663142700           99  
6   1663143000           99  
7   1663143300           99  
8   1663171200  -0.00172134  
9   1663171500           99  
10  1663171800           99  
11  1663172100           99  
12  1663200000  -0.00301937  
13  1663200300           99  
14  1663200600           99  
15  1663200900           99  
16  1663228800  -0.00216987  
17  1663229100           99  
18  1663229400           99  
19  1663229700           99

In [90]:
finalDict

{'ETHUSDT': [[-0.00111142, 1572.36, [1572.81, 1575.01, 1557.47]],
  [-0.00182506, 1610.15, [1602.37, 1588.54, 1589.81]],
  [-0.00172134, 1596.76, [1589.31, 1588.76, 1585.45]],
  [-0.00301937, 1639.03, [1633.6, 1634.25, 1636.9]],
  [-0.00216987, 1641.0, [1621.25, 1623.85, 1618.3]]],
 'ETCUSDT': [[-0.00251487, 34.264, [33.932, 33.933, 33.853]],
  [-0.00157957, 33.812, [33.541, 33.445, 33.411]],
  [-0.001153, 34.053, [34.635, 34.408, 34.228]],
  [-0.0010052, 33.975, [33.952, 33.868, 33.82]],
  [-0.00165888, 28.3, [28.176, 28.191, 28.35]],
  [-0.00249497, 29.935, [29.915, 29.869, 29.773]],
  [-0.00278547, 30.303, [30.312, 30.034, 29.912]],
  [-0.00109638, 29.447, [29.273, 29.336, 29.39]],
  [-0.00239283, 27.714, [27.682, 27.651, 27.568]],
  [-0.00196283, 28.561, [28.53, 28.391, 28.366]]],
 'XMRUSDT': [[-0.00114057, 158.03, [157.37, 157.21, 156.83]],
  [-0.0014707, 159.25, [158.43, 158.46, 158.34]],
  [-0.00110276, 159.8, [157.76, 156.8, 156.96]],
  [-0.0012831, 162.3, [162.28, 162.34, 162.

In [102]:
result = {}
tmpFund = []
tmpProfit = []
Fund = []
Profit = []
resultDf = pd.DataFrame()
for k, v in finalDict.items():
    tmpL = []
    for i in v:
        if i[0] < 0:
            spread = round((i[1] - min(i[2]))/i[1], 3)
        else:
            spread = round((max(i[2]) - i[1])/i[1], 3)
        tmpL.append([round(i[0], 4), spread])
        tmpFund.append(abs(round(i[0], 4)*100))
        tmpProfit.append(spread*100)
    result[k] = tmpL
    Fund += tmpFund
    Profit += tmpProfit
resultDf['Fund'] = Fund
resultDf['Profit'] = Profit

In [134]:
import plotly.express as px
import plotly.figure_factory as ff
df = px.data.medals_long()

fig = px.scatter(resultDf, y="Fund", x="Profit")
fig.update_traces(marker_size=4)

fig.add_shape(type="line",
    x0=0, y0=0, x1=2.5, y1=2.5,
    line=dict(color="LightSeaGreen",width=3)
)
fig.show()

/Users/jochien/opt/anaconda3/lib/python3.9/site-packages/scipy/__init__.py:146: UserWarning:

A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.23.3



In [133]:
resultDf['spread'] = resultDf['Profit'] - resultDf['Fund']
print('平均獲利: ', np.mean(resultDf['spread']))
print('最大獲利: ', np.max(resultDf['spread']))
print('最大虧損: ', np.min(resultDf['spread']))      
resultDf['win'] = resultDf['Profit'] > resultDf['Fund']
print('勝率: ', sum(resultDf['win'])/resultDf.shape[0])

step1 = resultDf[(resultDf['Fund'] >= 0.1) & (resultDf['Fund'] < 0.2)]
print('fund介於 0.1% ~ 0.2%勝率: ', sum(step1['win'])/step1.shape[0], '共{}交易'.format(step1.shape[0]))
step2 = resultDf[(resultDf['Fund'] >= 0.2) & (resultDf['Fund'] < 0.4)]
print('fund介於 0.2% ~ 0.4%勝率: ', sum(step2['win'])/step2.shape[0], '共{}交易'.format(step2.shape[0]))
step3 = resultDf[(resultDf['Fund'] >= 0.4) & (resultDf['Fund'] < 0.7)]
print('fund介於 0.4% ~ 0.7%勝率: ', sum(step3['win'])/step3.shape[0], '共{}交易'.format(step3.shape[0]))
step4 = resultDf[(resultDf['Fund'] >= 0.7) & (resultDf['Fund'] < 1)]
print('fund介於 0.7% ~ 1%勝率: ', sum(step4['win'])/step4.shape[0], '共{}交易'.format(step4.shape[0]))
step5 = resultDf[resultDf['Fund'] >= 1]
print('fund在1%以上勝率: ', sum(step5['win'])/step5.shape[0], '共{}交易'.format(step5.shape[0]))

平均獲利:  0.7290270601911775
最大獲利:  9.63
最大虧損:  -2.7
勝率:  0.8311159907000775
fund介於 0.1% ~ 0.2%勝率:  0.8343216812317936 共19224交易
fund介於 0.2% ~ 0.4%勝率:  0.835082655471005 共7622交易
fund介於 0.4% ~ 0.7%勝率:  0.7988269794721408 共1705交易
fund介於 0.7% ~ 1%勝率:  0.83729216152019 共1684交易
fund在1%以上勝率:  0.7667121418826739 共733交易


In [137]:
np.random.seed(1)

x = resultDf['spread']
hist_data = [x]
group_labels = ['distplot'] # name of the dataset

fig = ff.create_distplot(hist_data, group_labels)
fig.show()

In [ ]:
(dfObj['Sale'] > 30) & (dfObj['Sale'] < 33)

In [146]:
resultDf[resultDf['Fund'] == 0.1].describe()

Fund       Profit       spread
count  2.618000e+03  2618.000000  2618.000000
mean   1.000000e-01     0.735447     0.635447
std    3.428468e-15     0.636338     0.636338
min    1.000000e-01    -0.300000    -0.400000
25%    1.000000e-01     0.200000     0.100000
50%    1.000000e-01     0.800000     0.700000
75%    1.000000e-01     1.100000     1.000000
max    1.000000e-01     3.300000     3.200000

In [148]:
resultDf

Fund  Profit    win  spread
0      0.11     0.9   True    0.79
1      0.18     1.3   True    1.12
2      0.17     0.7   True    0.53
3      0.30     0.3  False    0.00
4      0.22     1.4   True    1.18
...     ...     ...    ...     ...
30963  0.25     3.4   True    3.15
30964  0.13     1.4   True    1.27
30965  0.19     0.5   True    0.31
30966  0.75     2.8   True    2.05
30967  0.20     1.5   True    1.30

[30968 rows x 4 columns]